# Can I walk to the train?
In this notebook we'll be exploring the walkability of Klang Valley's train stations using isochrone maps
We will use Open Route Service's API to draw this and compile the results into a csv
The data gathered will be visualized to be understood
KL has multiple different train lines with varying levels of service spreading across a large area. There is a relatively large number of stations relative to the population however the accesibility of the stations seems to be an issue for pedestrians. We'll analyze each train station from different lines. And compile them later on to get an average to be compared with other cities

In [1]:
#folium is the library used to visualize maps
import folium
#library to call Open Route Service(ORS)'s client and requests
from openrouteservice import client
import pandas as pd 
import numpy as np 
import plotly as py
#i like to be able to see all my columns in a pandas dataframe. this would allow it 
pd.set_option("display.max_columns", None)


# Train Station isochrones

Let's visualize all the stations and the 15 minute walking radius on a map.
15 minutes is somewhat arbitrary but given malaysia's hot weather it seems the most fair amount of time that malaysian's can generally tolerate to walk outdoors

In [149]:
api_key = '' #Provide your personal API key
clnt = client.Client(key=api_key) 


In [2]:
#loading up train station data. This file contains the csv data for KL train stations. 
file_url = '../resources/data/train_stations.csv'

data = pd.read_csv(file_url, index_col="Stop ID")
print(data.head())
print(data.columns)

                  Name  Service Provider Name  Latitude   Longitude ROUTE ID  \
Stop ID                                                                        
KC04       TAMAN WAHYU  Keretapi Tanah Melayu  3.214544  101.672182       KC   
KC03      KAMPUNG BATU  Keretapi Tanah Melayu  3.204796  101.675646       KC   
KB01        MID VALLEY  Keretapi Tanah Melayu  3.118528  101.678985       KB   
KC02     BATU KENTOMEN  Keretapi Tanah Melayu  3.198336  101.681163       KC   
KC05        BATU CAVES  Keretapi Tanah Melayu  3.237887  101.681187       KC   

            Route Name Line Number Line Colour Colour Hex Code  
Stop ID                                                         
KC04     Seremban Line           1        Blue         #0000FF  
KC03     Seremban Line           1        Blue         #0000FF  
KB01     Seremban Line           1        Blue         #0000FF  
KC02     Seremban Line           1        Blue         #0000FF  
KC05     Seremban Line           1        Blue   

In [3]:
#helper method to setup any input dataframe into dictionaries that can be input into OSR isochrone methods and folium maps
def dictSetup(dataframe):
    station_dict = dataframe.to_dict(orient='index')
    for name, station in station_dict.items():
        station['locations'] = [station['Longitude'],station['Latitude']]
    return station_dict

In [121]:
#Perform isochrone request and generates a new item in the stations dictionary containing isochrone data for that station.
#this will save the isochrones requested from Open Route Service in dictionaries that we created from dictSetup()
def isoGeoJsonRetriever(parameters,stations,client):
    for name, station in stations.items():
        print("Retrieving Isochrone of {} station".format(station['Name']))
        parameters['locations'] = [station['locations']]
        station['iso'] = client.isochrones(**parameters)
        print("Success")
    return
    

In [5]:
#helper method to create new dictionary that is a subset of the larger list of dictionaries
#used if you want to separate stations by station lines into smaller dictionaries 
def stationSubset(stations,station_list):
    return { your_key: stations[your_key] for your_key in station_list }



In [1]:
#input a Folium Map and Stations dictionary containing ISO data. this will draw the ISO lines on the folium map object
def isoVisualizer(maps,stations):
    import folium
    style_function = lambda x: {'color': '#4ef500' if x['properties']['value']<400 else ('#2100f5' if x['properties']['value']<700.0 else '#f50000'),
                                'fillOpacity' :0.25,
                                'weight':2,
                                'fillColor' :'#92daf0'}
                                                    #('#6234eb' if x['properties']['value']==600.0 else '#6234eb')
    
    for name, station in stations.items():
        folium.features.GeoJson(station['iso'],style_function = style_function).add_to(maps) # Add GeoJson to map
        folium.map.Marker(list(reversed(station['locations'])), # reverse coords due to weird folium lat/lon syntax
                            icon=folium.Icon(color='lightgray',
                                        icon_color='#cc0000',
                                        icon='train',
                                        prefix='fa',
                                            ),
                            popup=station['Name'],
                            ).add_to(maps) # Add apartment locations to map
    print("Done!")

All the helper methods above are used in the following function toMap(). All you need is:
dataframe with the columns - ['Name','Route Name','Latitude','Longitude'] that would be sufficient to draw isochrone maps for train stations.
param_iso - dictionary with the parameters of the isochrone
client - the open route service api column

In [2]:
def toMap(data,line,params_iso,client):
    # Set up folium map
    if not line in data.values:
        print('{} is not in data frame'.format(line))
        temp = data['Route Name'].unique()
        print('Choose from the following: ')
        print(temp)
        return
    if line != None:
        data = data[data['Route Name']==line]
    starting_location = (data['Latitude'].iloc[0],data['Longitude'].iloc[0])
    mapped = folium.Map(tiles='OpenStreetMap', location=starting_location, zoom_start=11)

    stations = dictSetup(data[data['Route Name']==line])

    isoGeoJsonRetriever(params_iso,stations,client)
    isoVisualizer(mapped,stations)
    return mapped,stations

In [43]:
#the way I coded this is that I want maps that will display train stations by lines. So that it wouldnt clutter the map.
lines = list(data['Route Name'].unique())
maps = []
params_iso = {'profile': 'foot-walking', 
              'range': [900], # 900/60 = 15 mins
              'interval': 300,
              'attributes': ['area', 'reachfactor', 'total_pop'] # Get population count for isochrones
             }
#By creating a list of train lines, i can iterate through each of them and create map objects for each train line.             
for line in lines:
    maps.append(toMap(data,line,params_iso,clnt))

Retrieving Isochrone of KC04 station
Success
Retrieving Isochrone of KC03 station
Success
Retrieving Isochrone of KB01 station
Success
Retrieving Isochrone of KC02 station
Success
Retrieving Isochrone of KC05 station
Success
Retrieving Isochrone of KB02 station
Success
Retrieving Isochrone of KC01 station
Success
Retrieving Isochrone of KA04 station
Success
Retrieving Isochrone of KA03 station
Success
Retrieving Isochrone of KA02 station
Success
Retrieving Isochrone of KB03 station
Success
Retrieving Isochrone of KB04 station
Success
Retrieving Isochrone of KB05 station
Success
Retrieving Isochrone of KB08 station
Success
Retrieving Isochrone of KB07 station
Success
Retrieving Isochrone of KB06 station
Success
Retrieving Isochrone of KB10 station
Success
Retrieving Isochrone of KB11 station
Success
Retrieving Isochrone of KB09 station
Success
Retrieving Isochrone of KB12 station
Success
Retrieving Isochrone of KB13 station
Success
Retrieving Isochrone of KB14 station
Success
Retrieving

Once all the Isochrone requests are completed, I would want to store the data first into CSVs for future references. The following helper functions will do that.

In [5]:
#Will store full isochrone data in a column. a bit messy but i wasn't sure the alternative to do this
def dictToDataFrame(maps,dataframe):
    iso_df = pd.DataFrame(columns= list(pd.DataFrame.from_dict(maps[0][1]).T)) 
    for i in range(len(maps)):
        temp = pd.DataFrame.from_dict(maps[i][1]).T
        iso_df = iso_df.append(temp)
    dataframe['iso']=iso_df['iso']     
    return dataframe 

In [6]:
# taking dataframe that now has the ISO, to parse isochrone data into dataframe columns containing relevant info such as walking coverage, population etc
def areaToDataframe(data):
    m2_to_km2 =1000000
    for station in data.index:
        iso = data.loc[station]['iso']
        if isinstance(iso, str):
            iso = eval(iso)
            area1 =  iso['features'][0]['properties']['area']/m2_to_km2 #area in iso is in m^2 Divide by 1000000 to get km^2
            area2 = (iso['features'][1]['properties']['area'])/m2_to_km2  #area in iso is in m^2 Divide by 1000000 to get km^2
            area3 = (iso['features'][2]['properties']['area'])/m2_to_km2 
            reach1 = (iso['features'][0]['properties']['reachfactor'])  
            reach2 = (iso['features'][1]['properties']['reachfactor']) 
            reach3 = (iso['features'][2]['properties']['reachfactor']) 
            pop1 = (iso['features'][0]['properties']['total_pop']) 
            pop2 = (iso['features'][1]['properties']['total_pop']) 
            pop3 = (iso['features'][2]['properties']['total_pop'])
        #for some reason errors keep popping out indicating key when trying to directly assign values to the data frame. so had to create separate variables and 
        # then assigning outside of if statement  
        elif isinstance(iso, dict):
            area1 =  iso['features'][0]['properties']['area']/m2_to_km2 #area in iso is in m^2 Divide by 1000000 to get km^2
            area2 = (iso['features'][1]['properties']['area'])/m2_to_km2  #area in iso is in m^2 Divide by 1000000 to get km^2
            area3 = (iso['features'][2]['properties']['area'])/m2_to_km2 
            reach1 = (iso['features'][0]['properties']['reachfactor'])  
            reach2 = (iso['features'][1]['properties']['reachfactor']) 
            reach3 = (iso['features'][2]['properties']['reachfactor']) 
            pop1 = (iso['features'][0]['properties']['total_pop']) 
            pop2 = (iso['features'][1]['properties']['total_pop']) 
            pop3 = (iso['features'][2]['properties']['total_pop'])
        #iso properties key ['group_index', 'value', 'center', 'area', 'reachfactor', 'total_pop']
        data.loc[station,'5 Minute Range Area'] = area1
        data.loc[station,'10 Minute Range Area'] = area2
        data.loc[station,'15 Minute Range Area'] = area3
        data.loc[station,'5 Minute Reach Factor'] = reach1
        data.loc[station,'10 Minute Reach Factor'] = reach2
        data.loc[station,'15 Minute Reach Factor'] = reach3
        data.loc[station,'5 Minute Population'] = pop1
        data.loc[station,'10 Minute Population'] = pop2
        data.loc[station,'15 Minute Population'] = pop3
    return data

In [ ]:
#saves the data with the isochrones  data into new csv files
data = dictToDataFrame(maps,data)
data.to_csv('train_stations_iso.csv')

In [111]:
#used to extract more specific data from isochrone data.
file_url = '../resources/data/train_stations_iso.csv'
data = pd.read_csv(file_url)
data  = areaToDataframe(data)
data.to_csv('../resources/data/train_stations_iso.csv')


In [80]:
maps[0][1].keys()

dict_keys(['KC04', 'KC03', 'KB01', 'KC02', 'KC05', 'KB02', 'KC01', 'KA04', 'KA03', 'KA02', 'KB03', 'KB04', 'KB05', 'KB08', 'KB07', 'KB06', 'KB10', 'KB11', 'KB09', 'KB12', 'KB13', 'KB14', 'KB15', 'KB16', 'KB17', 'KA01'])

In [45]:
maps[0][0]

In [64]:
maps[1]

In [65]:
maps[2]

In [66]:
maps[3]

In [67]:
maps[4]

In [68]:
maps[5]

In [69]:
maps[6]

In [70]:
maps[7]

In [71]:
maps[8]

In [72]:
maps[9]

In [73]:
maps[10]

# Singapore
Will be doing the same but with Singapore train station data

In [156]:
#loading up train station data.
file_url = '../resources/data/mrtsg.csv'

data_sg = pd.read_csv(file_url, index_col="OBJECTID")
lines = list(data_sg['Route Name'].unique())
map_sg = []
params_iso = {'profile': 'foot-walking', 
              'range': [900], # 900/60 = 15 mins
              'interval': 300,
              'attributes': ['area', 'reachfactor', 'total_pop'] # Get population count for isochrones
             }
for line in lines:
    map_sg.append(toMap(data_sg,line,params_iso,clnt))

In [321]:
#this is the overall map. Was done previously using slightly different code.
map_sg

In [152]:
map_sg[0][0]

In [153]:
map_sg[1][0]

In [141]:
map_sg[2][0]

In [142]:
map_sg[3][0]

In [143]:
map_sg[4][0]

In [144]:
map_sg[5][0]

In [145]:
map_sg[6][0]

In [146]:
map_sg[][0]

In [147]:
map_sg[8][0]

In [154]:
map_sg[9][0]

In [166]:
map_sg[10][0]

In [212]:
data_sg = dictToDataFrame(map_sg,data_sg)
data_sg

Name STN_NO           X           Y  \
OBJECTID                                                               
100             BENCOOLEN MRT STATION   DT21  29899.2575  31247.3368   
102             PROMENADE MRT STATION   DT15  31064.3414  30586.9146   
103                 BUGIS MRT STATION   DT14  30620.8769  31323.2495   
105            MACPHERSON MRT STATION   DT26  34235.7966  34256.4317   
114           JALAN BESAR MRT STATION   DT22  30466.0301  31970.4313   
...                               ...    ...         ...         ...   
89               RANGGUNG LRT STATION    SE5  35108.5942  40687.1255   
92               SENGKANG LRT STATION    STC  34913.5879  41502.6997   
175       WOODLANDS SOUTH MRT STATION    TE3  23607.8309  45444.7113   
181             WOODLANDS MRT STATION    TE2  22949.0322  46418.5578   
192       WOODLANDS MRT NORTH STATION    TE1         NaN         NaN   

          Latitude   Longitude  COLOR Colour Code               Route Name  \
OBJECTID                                                                     
100       1.298864  103.850380   BLUE     #0354a6            Downtown Line   
102       1.292892  103.860846   BLUE     #0354a6            Downtown Line   
103       1.299551  103.856862   BLUE     #0354a6            Downtown Line   
105       1.326077  103.889336   BLUE     #0354a6            Downtown Line   
114       1.305404  103.855471   BLUE     #0354a6            Downtown Line   
...            ...         ...    ...         ...                      ...   
89        1.384234  103.897176   GREY     #748477             Sengkang LRT   
92        1.391609  103.895424   GREY     #748477             Sengkang LRT   
175       1.427260  103.793863  BROWN     #734538  Thomson-East Coast Line   
181       1.436067  103.787945  BROWN     #734538  Thomson-East Coast Line   
192       1.448379  103.785647  BROWN     #734538  Thomson-East Coast Line   

         Unnamed: 10                                                iso  
OBJECTID                                                                 
100              DTL  {'type': 'FeatureCollection', 'features': [{'t...  
102              DTL  {'type': 'FeatureCollection', 'features': [{'t...  
103              DTL  {'type': 'FeatureCollection', 'features': [{'t...  
105              DTL  {'type': 'FeatureCollection', 'features': [{'t...  
114              DTL  {'type': 'FeatureCollection', 'features': [{'t...  
...              ...                                                ...  
89                SL  {'type': 'FeatureCollection', 'features': [{'t...  
92                SL  {'type': 'FeatureCollection', 'features': [{'t...  
175              TEL  {'type': 'FeatureCollection', 'features': [{'t...  
181              TEL  {'type': 'FeatureCollection', 'features': [{'t...  
192              TEL  {'type': 'FeatureCollection', 'features': [{'t...  

[188 rows x 11 columns]

In [299]:
#saving all the new sg data into a new csv with the isochrone data
data_sg= areaToDataframe(data_sg)
data_sg.to_csv('../resources/data/mrtsg_iso.csv')

# Montreal
Again same methodology but for Montreal

In [256]:
file_name_montreal = '../resources/data/montreal_metro.csv'

data_montreal = pd.read_csv(file_name_montreal, index_col="Stop ID")
print(data_montreal.head())
print(data_montreal.columns)

         Object ID         Name                               Odonym  \
Stop ID                                                                
G1               1    Angrignon  Boulevard Angrignon; Parc Angrignon   
G2               2         Monk                       Boulevard Monk   
G3               3    Jolicoeur                        Rue Jolicoeur   
G4               4       Verdun     Rue de Verdun; borough of Verdun   
G5               5  De L'Église                   Avenue de l'Église   

                                                  Namesake      Opened  \
Stop ID                                                                  
G1                Jean-Baptiste Angrignon, city councillor  03-09-1978   
G2                     James Monk, Quebec Attorney-General  03-09-1978   
G3                     Jean-Moïse Jolicoeur, parish priest  03-09-1978   
G4       Notre-Dame-de-Saverdun, France, hometown of Se...  03-09-1978   
G5                                       Église Sai

In [239]:
map_montreal = folium.Map(tiles='OpenStreetMap', location=(45.5017 , -73.5673), zoom_start=11)
stations_dict_montreal = dictSetup(data_montreal)
for name, station in stations_dict_montreal.items():
    folium.map.Marker(list(reversed(station['locations'])), # reverse coords due to weird folium lat/lon syntax
                        icon=folium.Icon(color='lightgray',
                                            icon_color='#cc0000',
                                            icon='home',
                                            prefix='fa',
                                        ),
                        popup=station['Name'],
                    ).add_to(map_montreal)
map_montreal

In [258]:
lines_montreal = list(data_montreal['Route Name'].unique())
maps_montreal = []
params_iso = {'profile': 'foot-walking', 
              'range': [900], # 900/60 = 15 mins
              'interval': 300,
              'attributes': ['area', 'reachfactor', 'total_pop'] # Get population count for isochrones
             }
for line in lines_montreal:
    maps_montreal.append(toMap(data_montreal,line,params_iso,clnt))

Retrieving Isochrone of G1 station
Success
Retrieving Isochrone of G2 station
Success
Retrieving Isochrone of G3 station
Success
Retrieving Isochrone of G4 station
Success
Retrieving Isochrone of G5 station
Success
Retrieving Isochrone of G6 station
Success
Retrieving Isochrone of G7 station
Success
Retrieving Isochrone of G8 station
Success
Retrieving Isochrone of G9 station
Success
Retrieving Isochrone of G10 station
Success
Retrieving Isochrone of G11 station
Success
Retrieving Isochrone of G12 station
Success
Retrieving Isochrone of G13 station
Success
Retrieving Isochrone of G14 station
Success
Retrieving Isochrone of G15 station
Success
Retrieving Isochrone of G18 station
Success
Retrieving Isochrone of G16 station
Success
Retrieving Isochrone of G17 station
Success
Retrieving Isochrone of G19 station
Success
Retrieving Isochrone of G20 station
Success
Retrieving Isochrone of G21 station
Success
Retrieving Isochrone of G22 station
Success
Retrieving Isochrone of G23 station
Succe

In [259]:
maps_montreal[0][0]

In [260]:
maps_montreal[1][0]

In [261]:
maps_montreal[2][0]

In [262]:
maps_montreal[3][0]

In [ ]:
data_montreal = dictToDataFrame(maps_montreal,data_montreal)
data_montreal.to_csv('montreal_metro_iso.csv')

In [301]:
data_montreal = pd.read_csv('../resources/data/montreal_metro_iso.csv')
data_montreal = areaToDataframe(data_montreal)
data_montreal.to_csv('../resources/data/montreal_metro_iso.csv')

# We've got isochrones!

We're done gathering data. Now to get some stats we'll be doing it in a different notebook as it's getting too long here